In [1]:
import json
import os
import random
import gc
from time import perf_counter as timer
import numpy as np

In [2]:
import sys
sys.path.insert(0, "/NS/llm-pretraining/work/afkhan/tokensmith")
sys.path.insert(0, "/NS/llm-pretraining/work/afkhan/USC_Colab/gpt-neox")

In [3]:
from transformers import AutoTokenizer
TOKENIZER_NAME_OR_PATH = "EleutherAI/gpt-neox-20b"
tokenizer = AutoTokenizer.from_pretrained(TOKENIZER_NAME_OR_PATH, add_eos_token=True)

/NS/venvs/work/afkhan/neox_updated_env/lib/python3.11/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [4]:
from tokensmith import DatasetManager

dataset_manager = DatasetManager()

[2025-07-03 09:45:58,738] [INFO] [real_accelerator.py:161:get_accelerator] Setting ds_accelerator to cuda (auto detect)


/NS/venvs/work/afkhan/neox_updated_env/lib/python3.11/site-packages/deepspeed/runtime/zero/linear.py:47: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @autocast_custom_fwd
/NS/venvs/work/afkhan/neox_updated_env/lib/python3.11/site-packages/deepspeed/runtime/zero/linear.py:66: FutureWarning: `torch.cuda.amp.custom_bwd(args...)` is deprecated. Please use `torch.amp.custom_bwd(args..., device_type='cuda')` instead.
  @autocast_custom_bwd


# Time Index Creation

In [5]:
# sizes = [1, 10, 100, 1000, 10000, 100000, 1000000]

# log_file = 'search_index_creation_log.txt'

# for size in sizes:
#     dataset_manager = DatasetManager()

#     bin_file_path = f"benchmarking_data/data_{size}_text_document.bin"
#     search_index_save_path = f"benchmarking_data/data_{size}_search_index_text_document.idx"

#     start_time = time.time()

#     dataset_manager.setup_search(
#         bin_file_path=bin_file_path,
#         search_index_save_path=search_index_save_path,
#         vocab=2**16,
#         verbose=False,
#         reuse=False,
#     )

#     end_time = time.time()

#     elapsed_time = end_time - start_time

#     with open(log_file, 'a') as f:
#         f.write(f"Size: {size}, Time taken: {elapsed_time} seconds\n")

# Time Inspect Operations

### Across Different Size Bin Files

In [6]:
import os
import random
import json
import numpy as np
from time import time as timer
import gc

# Assuming DatasetManager is defined elsewhere and imported
# from your_module import DatasetManager

sizes = [1, 10, 100, 1000, 10000, 100000, 1000000]

random.seed(42)
sample_ids = random.sample(range(1, 10000), 100)

log_file = 'logs/inspect_time_across_num_docs_logs.json'

# Initialize results dictionary
results = {
    "benchmark_type": "inspect_across_dataset_sizes",
    "sample_size": 100,
    "num_runs": 5,
    "timestamp": timer(),
    "results": []
}

for size in sizes:
    print(f"\n==== Running for dataset size: {size} ====")
    
    dataset_prefix = f"benchmarking_data/data_{size}_text_document"
    batch_info_save_prefix = f"benchmarking_data/batch_info_{size}"

    # Reinitialize DatasetManager for a clean state
    dataset_manager = DatasetManager()

    # --- Benchmark setup time ---
    gc.collect()
    setup_start = timer()
    dataset_manager.setup_edit_inspect_sample_export(
        dataset_prefix=dataset_prefix,
        batch_info_save_prefix=batch_info_save_prefix,
        train_iters=10000,
        train_batch_size=16,
        train_seq_len=2048,
        seed=42,
        splits_string='990,5,5',
        packing_impl='packed',
        allow_chopped=True,
    )
    setup_end = timer()
    setup_duration = setup_end - setup_start

    print(f"Setup time for size {size}: {setup_duration:.4f} seconds")

    # --- Warm-up call ---
    _ = dataset_manager.sample.get_samples_by_indices(indices=[0])

    # --- Benchmark sampling time (collect all runs) ---
    durations = []
    for run_idx in range(5):
        gc.collect()
        s = timer()
        dataset_manager.sample.get_samples_by_indices(indices=sample_ids)
        durations.append(timer() - s)

    avg_duration = sum(durations) / len(durations)
    variance = np.var(durations)

    # Store all data for this size
    size_result = {
        "dataset_size": size,
        "setup_time": setup_duration,
        "sampling_times": durations,
        "mean_sampling_time": avg_duration,
        "variance_sampling_time": variance,
        "min_sampling_time": min(durations),
        "max_sampling_time": max(durations)
    }
    
    results["results"].append(size_result)

    print(f"Avg sampling time for 100 samples (size {size}): {avg_duration} seconds | Variance: {variance}")

# Save results to JSON file
with open(log_file, 'w') as f:
    json.dump(results, f, indent=2)

print(f"\nResults saved to {log_file}")


==== Running for dataset size: 1 ====
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Setup time for size 1: 0.0095 seconds
Avg sampling time for 100 samples (size 1): 0.0039936542510986325 seconds | Variance: 4.062195785081713e-08

==== Running for dataset size: 10 ====
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Setup time for size 10: 0.0088 seconds
Avg sampling time for 100 samples (size 10): 0.0035613536834716796 seconds | Variance: 2.8407398531271613e-08

==== Running for dataset size: 100 ====
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Setup time for size 100: 0.0079 seconds
Avg sampling time for 100 samples (size 100): 0.0031635284423828123 seconds | Variance: 3.931357696274063e-08

==== Running for dataset size: 1000 ====
    warming up index mmap file...
    reading sizes...
    reading

### Across Different Numbers of Samples

In [7]:
samples = [1, 10, 100, 1000, 10000]

size = 1000000

dataset_prefix = f"benchmarking_data/data_{size}_text_document"

batch_info_save_prefix = f"benchmarking_data/batch_info_{size}"

log_file = 'logs/inspect_time_across_num_samples_log.json'

# Initialize results dictionary
results = {
    "benchmark_type": "inspect_across_sample_sizes",
    "dataset_size": size,
    "num_runs": 5,
    "timestamp": timer(),
    "results": []
}

from time import perf_counter as timer
import gc

for sample in samples:
    random.seed(42)
    sample_ids = random.sample(range(1, 100000), sample)

    # Optional: re-init dataset manager for fresh state
    dataset_manager = DatasetManager()
    dataset_manager.setup_edit_inspect_sample_export(
        dataset_prefix=dataset_prefix,
        batch_info_save_prefix=batch_info_save_prefix,
        train_iters=100000, # Set to a large number to ensure all locations are inspectable
        train_batch_size=16,
        train_seq_len=2048,
        seed=42,
        splits_string='990,5,5',
        packing_impl='packed',
        allow_chopped=True,
    )

    # Warm-up call
    _ = dataset_manager.sample.get_samples_by_indices(indices=[0])

    durations = []
    for run_idx in range(5):
        gc.collect()
        start = timer()
        dataset_manager.sample.get_samples_by_indices(indices=sample_ids)
        durations.append(timer() - start)

    avg_time = sum(durations) / len(durations)
    variance = np.var(durations)

    # Store all data for this sample size
    sample_result = {
        "sample_size": sample,
        "sampling_times": durations,
        "mean_sampling_time": avg_time,
        "variance_sampling_time": variance,
        "min_sampling_time": min(durations),
        "max_sampling_time": max(durations)
    }
    
    results["results"].append(sample_result)

    print(f"Sample size {sample}: Avg time = {avg_time}s | Variance: {variance}")

# Save results to JSON file
with open(log_file, 'w') as f:
    json.dump(results, f, indent=2)

print(f"\nResults saved to {log_file}")


    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Sample size 1: Avg time = 0.0001967770978808403s | Variance: 2.2790558276489236e-08
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Sample size 10: Avg time = 0.007817060500383378s | Variance: 8.905222344930684e-08
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Sample size 100: Avg time = 0.07221241928637027s | Variance: 4.22631534155879e-06
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Sample size 1000: Avg time = 0.6513968104496598s | Variance: 0.0003201480910466495
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...
Sample size 10000: Avg time = 6.492952901497484s | Variance: 0.0007011711291758626

Results saved to logs/inspect_time_acro

# Time Edit Operations

### Across Different Size Bin Files

In [8]:
sizes = [1, 10, 100, 1000, 10000, 100000, 1000000]

random.seed(42)
edit_locations = random.sample(range(2, 10000), 100)

injection_data = []

for loc in edit_locations:
    injection_data.append({
        "text": "This is a test sentence.",
        "injection_loc": loc,
        "injection_type": "seq_shuffle",
    })

warmup_edit_location = 1

log_file = 'logs/edit_time_across_num_docs_logs.json'

# Initialize results dictionary
results = {
    "benchmark_type": "edit_across_dataset_sizes",
    "num_edits": 100,
    "num_runs": 5,
    "timestamp": timer(),
    "results": []
}

for size in sizes:
    print(f"\n==== Running for dataset size: {size} ====")
    
    dataset_prefix = f"benchmarking_data/data_{size}_text_document"
    batch_info_save_prefix = f"benchmarking_data/batch_info_{size}"

    # Reinitialize DatasetManager for a clean state
    dataset_manager = DatasetManager()

    # --- Benchmark setup time ---
    gc.collect()
    setup_start = timer()
    dataset_manager.setup_edit_inspect_sample_export(
        dataset_prefix=dataset_prefix,
        batch_info_save_prefix=batch_info_save_prefix,
        train_iters=10000,
        train_batch_size=16,
        train_seq_len=2048,
        seed=42,
        splits_string='990,5,5',
        packing_impl='packed',
        allow_chopped=True,
    )
    setup_end = timer()
    setup_duration = setup_end - setup_start

    print(f"Setup time for size {size}: {setup_duration:.4f} seconds")

    RNG = np.random.default_rng(42)
    
    # --- Warm-up call ---
    _ = dataset_manager.edit.inject_and_preview(
        text = 'This is a test sentence.',
        tokenizer=tokenizer,
        injection_loc=warmup_edit_location,
        injection_type="seq_start",
        rng=RNG,
        add_eos_token=True,
        dry_run=False,
    )

    # --- Benchmark editing time (collect all runs) ---
    durations = []
    for run_idx in range(5):
        gc.collect()
        s = timer()
        
        _ = dataset_manager.edit.inject_multiple_samples(
            injections = injection_data,
            tokenizer=tokenizer,
            rng=RNG,
            add_eos_token=True,
            dry_run=False,
    )

        durations.append(timer() - s)

    avg_duration = sum(durations) / len(durations)
    variance = np.var(durations)

    # Store all data for this size
    size_result = {
        "dataset_size": size,
        "setup_time": setup_duration,
        "editing_times": durations,
        "mean_editing_time": avg_duration,
        "variance_editing_time": variance,
        "min_editing_time": min(durations),
        "max_editing_time": max(durations)
    }
    
    results["results"].append(size_result)

    print(f"Avg editing time for 100 samples (size {size}): {avg_duration} seconds | Variance: {variance}")

# Save results to JSON file
with open(log_file, 'w') as f:
    json.dump(results, f, indent=2)

print(f"\nResults saved to {log_file}")


==== Running for dataset size: 1 ====
    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...


>> Casting injection data from int64 to <class 'numpy.uint16'>
This warning will not be shown again. The process will wait for 10 seconds before starting the edit process.


Setup time for size 1: 0.0069 seconds
Dummy sample: [1552  310  247 1071 6197   15    0]
Training sample 1
Sample consists of segments from 3 documents
Raw sample: [ 247 1071 6197 ...   15    0  247]
---
Decoded sample:  a test sentence.<|endoftext|> is a test sentence.<|endoftext|>This is a test sentence.<|endoftext|>This is a test sentence.<|endoftext|>This is a test sentence.<|endoftext|>This is a testThis isThisThis is a test sentence.<|endoftext|> sentence.This is aThis sentence.<|endoftext|>.<|endoftext|>.ThisThis is aThis is a test sentence.<|endoftext|> test sentence.<|endoftext|>This is a test sentence.<|endoftext|> is a test sentence.<|endoftext|><|endoftext|><|endoftext|>This.This.<|endoftext|> sentenceThis is test sentence.<|endoftext|><|endoftext|> a test sentence. sentence sentence test sentence..<|endoftext|> isThis isThis<|endoftext|>ThisThisThis is a test sentenceThis is a test sentence.<|endoftext|>.<|endoftext|>This is a test sentence.<|endoftext|> is a test sentence

>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.u

Training sample 1 after injection
Raw sample: [1552  310  247 ...   15    0  247]
---
Decoded sample: This is a test sentence.<|endoftext|> test sentence.<|endoftext|>This is a test sentence.<|endoftext|>This is a test sentence.<|endoftext|>This is a test sentence.<|endoftext|>This is a testThis isThisThis is a test sentence.<|endoftext|> sentence.This is aThis sentence.<|endoftext|>.<|endoftext|>.ThisThis is aThis is a test sentence.<|endoftext|> test sentence.<|endoftext|>This is a test sentence.<|endoftext|> is a test sentence.<|endoftext|><|endoftext|><|endoftext|>This.This.<|endoftext|> sentenceThis is test sentence.<|endoftext|><|endoftext|> a test sentence. sentence sentence test sentence..<|endoftext|> isThis isThis<|endoftext|>ThisThisThis is a test sentenceThis is a test sentence.<|endoftext|>.<|endoftext|>This is a test sentence.<|endoftext|> is a test sentence.<|endoftext|> is a testThis is a test sentence.<|endoftext|>This is aThis isThis is a test sentence.<|endoftext|> a

...

=== Injection 52/100 ===
=== Injection 53/100 ===
=== Injection 54/100 ===
=== Injection 55/100 ===
=== Injection 56/100 ===
=== Injection 57/100 ===
=== Injection 58/100 ===
=== Injection 59/100 ===
=== Injection 60/100 ===
=== Injection 61/100 ===
=== Injection 62/100 ===
=== Injection 63/100 ===
=== Injection 64/100 ===
=== Injection 65/100 ===
=== Injection 66/100 ===
=== Injection 67/100 ===
=== Injection 68/100 ===
=== Injection 69/100 ===
=== Injection 70/100 ===
=== Injection 71/100 ===
=== Injection 72/100 ===
=== Injection 73/100 ===
=== Injection 74/100 ===
=== Injection 75/100 ===
=== Injection 76/100 ===
=== Injection 77/100 ===
=== Injection 78/100 ===
=== Injection 79/100 ===
=== Injection 80/100 ===
=== Injection 81/100 ===
=== Injection 82/100 ===
=== Injection 83/100 ===
=== Injection 84/100 ===
=== Injection 85/100 ===
=== Injection 86/100 ===
=== Injection 87/100 ===
=== Injection 88/100 ===
=== Injection 89/100 ===
=== Injection 90/100 ===
=== Injection 91/100 ===


>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.u

=== Injection 1/100 ===
=== Injection 2/100 ===
=== Injection 3/100 ===
=== Injection 4/100 ===
=== Injection 5/100 ===
=== Injection 6/100 ===
=== Injection 7/100 ===
=== Injection 8/100 ===
=== Injection 9/100 ===
=== Injection 10/100 ===
=== Injection 11/100 ===
=== Injection 12/100 ===
=== Injection 13/100 ===
=== Injection 14/100 ===
=== Injection 15/100 ===
=== Injection 16/100 ===
=== Injection 17/100 ===
=== Injection 18/100 ===
=== Injection 19/100 ===
=== Injection 20/100 ===
=== Injection 21/100 ===
=== Injection 22/100 ===
=== Injection 23/100 ===
=== Injection 24/100 ===
=== Injection 25/100 ===
=== Injection 26/100 ===
=== Injection 27/100 ===
=== Injection 28/100 ===
=== Injection 29/100 ===
=== Injection 30/100 ===
=== Injection 31/100 ===
=== Injection 32/100 ===
=== Injection 33/100 ===
=== Injection 34/100 ===
=== Injection 35/100 ===
=== Injection 36/100 ===
=== Injection 37/100 ===
=== Injection 38/100 ===
=== Injection 39/100 ===
=== Injection 40/100 ===
=== Injec

>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.u

=== Injection 51/100 ===
=== Injection 52/100 ===
=== Injection 53/100 ===
=== Injection 54/100 ===
=== Injection 55/100 ===
=== Injection 56/100 ===
=== Injection 57/100 ===
=== Injection 58/100 ===
=== Injection 59/100 ===
=== Injection 60/100 ===
=== Injection 61/100 ===
=== Injection 62/100 ===
=== Injection 63/100 ===
=== Injection 64/100 ===
=== Injection 65/100 ===
=== Injection 66/100 ===
=== Injection 67/100 ===
=== Injection 68/100 ===
=== Injection 69/100 ===
=== Injection 70/100 ===
=== Injection 71/100 ===
=== Injection 72/100 ===
=== Injection 73/100 ===
=== Injection 74/100 ===
=== Injection 75/100 ===
=== Injection 76/100 ===
=== Injection 77/100 ===
=== Injection 78/100 ===
=== Injection 79/100 ===
=== Injection 80/100 ===
=== Injection 81/100 ===
=== Injection 82/100 ===
=== Injection 83/100 ===
=== Injection 84/100 ===
=== Injection 85/100 ===
=== Injection 86/100 ===
=== Injection 87/100 ===
=== Injection 88/100 ===
=== Injection 89/100 ===
=== Injection 90/100 ===


### Across Different Numbers of Samples

In [9]:
samples = [1, 10, 100, 1000, 10000]

size = 1000000

dataset_prefix = f"benchmarking_data/data_{size}_text_document"

batch_info_save_prefix = f"benchmarking_data/batch_info_{size}"

log_file = 'logs/edit_time_across_num_samples_log.json'

warmup_edit_location = 1

# Initialize results dictionary
results = {
    "benchmark_type": "edit_across_sample_sizes",
    "dataset_size": size,
    "num_runs": 5,
    "timestamp": timer(),
    "results": []
}

RNG = np.random.default_rng(42)

for sample in samples:
    random.seed(42)
    edit_locations = random.sample(range(2, 100000), sample)

    assert len(edit_locations) == sample, f"Sample size {sample} does not match number of sample IDs generated: {len(edit_locations)}"

    injection_data = []
    for loc in edit_locations:
        injection_data.append({
            "text": "This is a test sentence.",
            "injection_loc": loc,
            "injection_type": "seq_shuffle",
        })

    # Optional: re-init dataset manager for fresh state
    dataset_manager = DatasetManager()
    dataset_manager.setup_edit_inspect_sample_export(
        dataset_prefix=dataset_prefix,
        batch_info_save_prefix=batch_info_save_prefix,
        train_iters=100000, # Set to a large number to ensure all locations are inspectable
        train_batch_size=16,
        train_seq_len=2048,
        seed=42,
        splits_string='990,5,5',
        packing_impl='packed',
        allow_chopped=True,
    )

    # Warm-up call
    _ = dataset_manager.edit.inject_and_preview(
        text = 'This is a test sentence.',
        tokenizer=tokenizer,
        injection_loc=warmup_edit_location,
        injection_type="seq_start",
        rng=RNG,
        add_eos_token=True,
        dry_run=False,
    )

    durations = []
    for run_idx in range(5):
        gc.collect()
        start = timer()
        dataset_manager.edit.inject_multiple_samples(
            injections = injection_data,
            tokenizer=tokenizer,
            rng=RNG,
            add_eos_token=True,
            dry_run=False,
        )
        durations.append(timer() - start)

    avg_time = sum(durations) / len(durations)
    variance = np.var(durations)

    # Store all data for this sample size
    sample_result = {
        "sample_size": sample,
        "editing_times": durations,
        "mean_editing_time": avg_time,
        "variance_editing_time": variance,
        "min_editing_time": min(durations),
        "max_editing_time": max(durations)
    }
    
    results["results"].append(sample_result)

    print(f"Sample size {sample}: Avg time = {avg_time}s | Variance: {variance}")

# Save results to JSON file
with open(log_file, 'w') as f:
    json.dump(results, f, indent=2)

print(f"\nResults saved to {log_file}")


    warming up index mmap file...
    reading sizes...
    reading pointers...
    reading document index...


>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>


Dummy sample: [1552  310  247 1071 6197   15    0]
Training sample 1
Sample consists of segments from 1 documents
Raw sample: [ 1552   310   247 ... 14285   323  6729]
---
Decoded sample: This is a test sentence.<|endoftext|> children in homes where there was a mom and a dad on a preferential basis.

Absolutely extraordinary. We have to have individuals that will stand up for religious conscience, and I did and I will again as president.


KING: Mr. Speaker? GINGRICH: Well, the reports we got were quite clear that the public health department was prepared to give a waiver to Catholic hospitals about a morning-after abortion pill, and that the governor's office issued explicit instructions saying that they believed it wasn't possible under Massachusetts law to give them that waiver. Now, that was the newspaper reports that came out. That's something that both Senator Santorum and I have raised before. But I want to go a step further, because this makes a point that Ron Paul has been mak

>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>


=== Injection 1/1 ===
=== Injection 1/1 ===
=== Injection 1/1 ===


...

=== Injection 9847/10000 ===
=== Injection 9848/10000 ===
=== Injection 9849/10000 ===
=== Injection 9850/10000 ===
=== Injection 9851/10000 ===
=== Injection 9852/10000 ===
=== Injection 9853/10000 ===
=== Injection 9854/10000 ===
=== Injection 9855/10000 ===
=== Injection 9856/10000 ===
=== Injection 9857/10000 ===
=== Injection 9858/10000 ===
=== Injection 9859/10000 ===
=== Injection 9860/10000 ===
=== Injection 9861/10000 ===
=== Injection 9862/10000 ===
=== Injection 9863/10000 ===
=== Injection 9864/10000 ===
=== Injection 9865/10000 ===
=== Injection 9866/10000 ===
=== Injection 9867/10000 ===
=== Injection 9868/10000 ===
=== Injection 9869/10000 ===
=== Injection 9870/10000 ===
=== Injection 9871/10000 ===
=== Injection 9872/10000 ===
=== Injection 9873/10000 ===
=== Injection 9874/10000 ===
=== Injection 9875/10000 ===
=== Injection 9876/10000 ===
=== Injection 9877/10000 ===
=== Injection 9878/10000 ===
=== Injection 9879/10000 ===
=== Injection 9880/10000 ===
=== Injection 

>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.u

=== Injection 9903/10000 ===
=== Injection 9904/10000 ===
=== Injection 9905/10000 ===
=== Injection 9906/10000 ===
=== Injection 9907/10000 ===
=== Injection 9908/10000 ===
=== Injection 9909/10000 ===
=== Injection 9910/10000 ===
=== Injection 9911/10000 ===
=== Injection 9912/10000 ===
=== Injection 9913/10000 ===
=== Injection 9914/10000 ===
=== Injection 9915/10000 ===
=== Injection 9916/10000 ===
=== Injection 9917/10000 ===
=== Injection 9918/10000 ===
=== Injection 9919/10000 ===
=== Injection 9920/10000 ===
=== Injection 9921/10000 ===
=== Injection 9922/10000 ===
=== Injection 9923/10000 ===
=== Injection 9924/10000 ===
=== Injection 9925/10000 ===
=== Injection 9926/10000 ===
=== Injection 9927/10000 ===
=== Injection 9928/10000 ===
=== Injection 9929/10000 ===
=== Injection 9930/10000 ===
=== Injection 9931/10000 ===
=== Injection 9932/10000 ===
=== Injection 9933/10000 ===
=== Injection 9934/10000 ===
=== Injection 9935/10000 ===
=== Injection 9936/10000 ===
=== Injection 

>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.uint16'>
>> Casting injection data from int64 to <class 'numpy.u

=== Injection 9957/10000 ===
=== Injection 9958/10000 ===
=== Injection 9959/10000 ===
=== Injection 9960/10000 ===
=== Injection 9961/10000 ===
=== Injection 9962/10000 ===
=== Injection 9963/10000 ===
=== Injection 9964/10000 ===
=== Injection 9965/10000 ===
=== Injection 9966/10000 ===
=== Injection 9967/10000 ===
=== Injection 9968/10000 ===
=== Injection 9969/10000 ===
=== Injection 9970/10000 ===
=== Injection 9971/10000 ===
=== Injection 9972/10000 ===
=== Injection 9973/10000 ===
=== Injection 9974/10000 ===
=== Injection 9975/10000 ===
=== Injection 9976/10000 ===
=== Injection 9977/10000 ===
=== Injection 9978/10000 ===
=== Injection 9979/10000 ===
=== Injection 9980/10000 ===
=== Injection 9981/10000 ===
=== Injection 9982/10000 ===
=== Injection 9983/10000 ===
=== Injection 9984/10000 ===
=== Injection 9985/10000 ===
=== Injection 9986/10000 ===
=== Injection 9987/10000 ===
=== Injection 9988/10000 ===
=== Injection 9989/10000 ===
=== Injection 9990/10000 ===
=== Injection 